# Jeopardy Review

<img src="http://upload.wikimedia.org/wikipedia/commons/d/d8/Jeopardy_game_board.png"/>

To run the code below, change the file from among [game1.csv](game1.csv), [game2.csv](game2.csv), and [game3.csv](game3.csv).

Click 6 times to see the categories.

Team A uses 'w' to buzz in.

Team B uses 'g' to buzz in.

Spacebar will go to the next screen. Click again to go back.

In [1]:
import processing.table.*;

Table table = loadTable("game1.csv", "header");
PFont fontA = loadFont("Arial");

String[] categories = new String[6];
int score_a = 0;
int score_b = 0;
int reveal = 0;
int[][] boxes = new int[6][5];
String[][] answers = new String[6][5];
String[][] questions = new String[6][5];
int showing_category = -1;
int showing_row = -1;
String pressed = "";

boolean arrayContains(String[] array, String search) {
    for (int i = 0; i < array.length; i++) {
        if (array[i] == search)
            return true;
    }
    return false;
}

void setup() {
    size(640, 480);
    // pick 6 unique categories:
    for (int i = 0; i < 6; i++) {
        int row_pos = int(random(0, table.getRowCount()));
        TableRow row = table.rows().get(row_pos);
        String cat = row.getString("Category");
        while (arrayContains(categories, cat)) {
            row_pos = int(random(0, table.getRowCount()));
            row = table.rows().get(row_pos);
            cat = row.getString("Category");
        }
        categories[i] = cat;
        // pick one q/a per topic/level:
        for (int j = 1; j <= 5; j++) {
            ArrayList choices = new ArrayList();
            int rows = 0;
            for (TableRow trow: table.rows()) {
                if (trow.getString("Category") == categories[i] && trow.getInt("Level") == j) {
                    choices.add(rows);
                }
                rows++;
            }
            if (choices.size() == 0) {
                println("Error in Category: " + categories[i] + ", level: " + j + ", count: " + choices.size());
            } else {
                // pick one
                int pickone = int(random(0, choices.size()));
                rows = choices.get(pickone);
                answers[i][j - 1] = table.rows().get(rows).getString("Answer");
                questions[i][j - 1] = table.rows().get(rows).getString("Question");
            }
        }
    }
    // Set up text defaults:
    textFont(fontA, 18);
    textAlign(CENTER, CENTER);
}

void draw() {
    int boxw = width/6.1;
    int boxh= height/8;
    background(127);
    fill(0);
    // categories:
    rect(5, 5, width - 10, boxh + 10);
    // q/a:
    rect(5, boxh * 1.5 - 5, width - 10, height - boxh - 70);
    // scores:
    rect(5, height - 40, width/2 - 10, 35);
    rect(width/2 + 5, height - 40, width/2 - 10, 35);
    fill(255, 201, 14); // yellow
    textAlign(LEFT, CENTER);
    text("Team A:", 5, height - 40, width/2 - 10, 35);
    text("Team B:", width/2 + 5, height - 40, width/2 - 10, 35);
    textAlign(RIGHT, CENTER);
    if (score_a >= 0) {
        text("$" + score_a, 5, height - 40, width/2 - 10, 35);
    } else {
        text("-$" + (-score_a), 5, height - 40, width/2 - 10, 35);
    }
    if (score_b >= 0) {
        text("$" + score_b, width/2 + 5, height - 40, width/2 - 10, 35);
    } else {
        text("-$" + (-score_b), width/2 + 5, height - 40, width/2 - 10, 35);
    }
    textAlign(CENTER, CENTER);
    // Boxes:
    for (int i=0; i < 6; i++) {
        fill(63, 72, 204); // blue
        rect(i * boxw + 10, 10, boxw - 10, boxh);
        fill(255, 201, 14); // yellow
        if (i < reveal)
            text(categories[i], i * boxw + 10, 5, boxw - 10, boxh);
    }
    for (int x=0; x < 6; x++) {
        for (int y=0; y < 5; y++) {
            fill(63, 72, 204); // blue
            rect(x * boxw + 10, y * (boxh + 10) + boxh * 1.5, boxw - 10, boxh);
            fill(255, 201, 14); // yellow
            if (x < reveal && boxes[x][y] == 0) {
                text("$" + ((y  + 1) * 100), 
                     x * boxw + 10, y * (boxh + 10) + boxh * 1.5, 
                     boxw - 10, boxh);
            }
        }
    }
    if (showing_category >= 0 && showing_row >= 0) {
        textAlign(CENTER, CENTER);
        fill(63/2, 72/2, 204/2); // blue
        rect(50, 50, width - 100, height - 150);
        fill(255, 201, 14); // yellow
        text(categories[showing_category] + " for $" + ((showing_row + 1) * 100), 50, 30, width - 100, 100);
        String answer = answers[showing_category][showing_row];
        textFont(fontA, 32);
        text(answer, 50, 50, width - 100, height - 150);
        textFont(fontA, 18);
        if (pressed == "A") {
            text("Team A buzzes in! Correct? y/n", 50, height - 200, width - 100, 100);
        } else if (pressed == "B") {
            text("Team B buzzes in! Correct? y/n", 50, height - 200, width - 100, 100);
        } else if (pressed == "answer") {
            text(questions[showing_category][showing_row], 50, height - 200, width - 100, 100);
        }
    }
}

void mousePressed() {
    int boxw = width/6.1;
    int boxh= height/8;
    if (reveal < 6) {
        reveal++;
    } else if (showing_category >= 0 && showing_row >= 0) {
        showing_category = -1;
        showing_row = -1;
    } else {
        // playing the game
        int category = int((mouseX - 10)/(boxw));
        int row = int((mouseY - boxh * 1.5)/(boxh + 10));
        //println("Category: " + category + " row: " + row);
        if (category >= 0 && category < 6) {
            if (row >= 0 && row < 5) {
                showing_category = category;
                showing_row = row;
                pressed = "";
            } else {
                showing_category = -1;
                showing_row = -1;
            }
        } else {
            showing_category = -1;
            showing_row = -1;
        }
    }
}

void keyPressed() {
    // w is 87
    // a is 65
    // s is 83
    // d is 68
    // f is 70
    // g is 71
    if (showing_category >= 0 && showing_category < 6) { 
        if (pressed == "") {
            if (keyCode == 87) { // w
                pressed = "A";
            } else if (keyCode == 71) { // g
                pressed = "B";
            } else if (keyCode == 32) {
                pressed = "answer";
            }
        } else if (pressed == "A") {
            if (keyCode == 89) { // y correct
                score_a += (showing_row + 1) * 100;
                pressed = "answer";
            } else if (keyCode == 78) { // n wrong
                score_a -= (showing_row + 1) * 100;
                pressed = "B";
            } else if (keyCode == 32) {
                pressed = "answer";
            }
        } else if (pressed == "B") {
            if (keyCode == 89) { // y correct
                score_b += (showing_row + 1) * 100;
                pressed = "answer";
            } else if (keyCode == 78) { // n wrong
                score_b -= (showing_row + 1) * 100;
                pressed = "A";
            } else if (keyCode == 32) {
                pressed = "answer";
            }
        } else if (pressed == "answer") {
            if (keyCode == 32) {
                boxes[showing_category][showing_row] = 1;
                pressed = "";
                showing_category = -1;
                showing_row = -1;
            }
        }
    } 
}

In [2]:
import processing.table.*;

Table table = loadTable("game2.csv", "header");
PFont fontA = loadFont("Arial");

String[] categories = new String[6];
int score_a = 0;
int score_b = 0;
int reveal = 0;
int[][] boxes = new int[6][5];
String[][] answers = new String[6][5];
String[][] questions = new String[6][5];
int showing_category = -1;
int showing_row = -1;
String pressed = "";

boolean arrayContains(String[] array, String search) {
    for (int i = 0; i < array.length; i++) {
        if (array[i] == search)
            return true;
    }
    return false;
}

void setup() {
    size(640, 480);
    // pick 6 unique categories:
    for (int i = 0; i < 6; i++) {
        int row_pos = int(random(0, table.getRowCount()));
        TableRow row = table.rows().get(row_pos);
        String cat = row.getString("Category");
        while (arrayContains(categories, cat)) {
            row_pos = int(random(0, table.getRowCount()));
            row = table.rows().get(row_pos);
            cat = row.getString("Category");
        }
        categories[i] = cat;
        // pick one q/a per topic/level:
        for (int j = 1; j <= 5; j++) {
            ArrayList choices = new ArrayList();
            int rows = 0;
            for (TableRow trow: table.rows()) {
                if (trow.getString("Category") == categories[i] && trow.getInt("Level") == j) {
                    choices.add(rows);
                }
                rows++;
            }
            if (choices.size() == 0) {
                println("Error in Category: " + categories[i] + ", level: " + j + ", count: " + choices.size());
            } else {
                // pick one
                int pickone = int(random(0, choices.size()));
                rows = choices.get(pickone);
                answers[i][j - 1] = table.rows().get(rows).getString("Answer");
                questions[i][j - 1] = table.rows().get(rows).getString("Question");
            }
        }
    }
    // Set up text defaults:
    textFont(fontA, 18);
    textAlign(CENTER, CENTER);
}

void draw() {
    int boxw = width/6.1;
    int boxh= height/8;
    background(127);
    fill(0);
    // categories:
    rect(5, 5, width - 10, boxh + 10);
    // q/a:
    rect(5, boxh * 1.5 - 5, width - 10, height - boxh - 70);
    // scores:
    rect(5, height - 40, width/2 - 10, 35);
    rect(width/2 + 5, height - 40, width/2 - 10, 35);
    fill(255, 201, 14); // yellow
    textAlign(LEFT, CENTER);
    text("Team A:", 5, height - 40, width/2 - 10, 35);
    text("Team B:", width/2 + 5, height - 40, width/2 - 10, 35);
    textAlign(RIGHT, CENTER);
    if (score_a >= 0) {
        text("$" + score_a, 5, height - 40, width/2 - 10, 35);
    } else {
        text("-$" + (-score_a), 5, height - 40, width/2 - 10, 35);
    }
    if (score_b >= 0) {
        text("$" + score_b, width/2 + 5, height - 40, width/2 - 10, 35);
    } else {
        text("-$" + (-score_b), width/2 + 5, height - 40, width/2 - 10, 35);
    }
    textAlign(CENTER, CENTER);
    // Boxes:
    for (int i=0; i < 6; i++) {
        fill(63, 72, 204); // blue
        rect(i * boxw + 10, 10, boxw - 10, boxh);
        fill(255, 201, 14); // yellow
        if (i < reveal)
            text(categories[i], i * boxw + 10, 5, boxw - 10, boxh);
    }
    for (int x=0; x < 6; x++) {
        for (int y=0; y < 5; y++) {
            fill(63, 72, 204); // blue
            rect(x * boxw + 10, y * (boxh + 10) + boxh * 1.5, boxw - 10, boxh);
            fill(255, 201, 14); // yellow
            if (x < reveal && boxes[x][y] == 0) {
                text("$" + ((y  + 1) * 100), 
                     x * boxw + 10, y * (boxh + 10) + boxh * 1.5, 
                     boxw - 10, boxh);
            }
        }
    }
    if (showing_category >= 0 && showing_row >= 0) {
        textAlign(CENTER, CENTER);
        fill(63/2, 72/2, 204/2); // blue
        rect(50, 50, width - 100, height - 150);
        fill(255, 201, 14); // yellow
        text(categories[showing_category] + " for $" + ((showing_row + 1) * 100), 50, 30, width - 100, 100);
        String answer = answers[showing_category][showing_row];
        textFont(fontA, 32);
        text(answer, 50, 50, width - 100, height - 150);
        textFont(fontA, 18);
        if (pressed == "A") {
            text("Team A buzzes in! Correct? y/n", 50, height - 200, width - 100, 100);
        } else if (pressed == "B") {
            text("Team B buzzes in! Correct? y/n", 50, height - 200, width - 100, 100);
        } else if (pressed == "answer") {
            text(questions[showing_category][showing_row], 50, height - 200, width - 100, 100);
        }
    }
}

void mousePressed() {
    int boxw = width/6.1;
    int boxh= height/8;
    if (reveal < 6) {
        reveal++;
    } else if (showing_category >= 0 && showing_row >= 0) {
        showing_category = -1;
        showing_row = -1;
    } else {
        // playing the game
        int category = int((mouseX - 10)/(boxw));
        int row = int((mouseY - boxh * 1.5)/(boxh + 10));
        //println("Category: " + category + " row: " + row);
        if (category >= 0 && category < 6) {
            if (row >= 0 && row < 5) {
                showing_category = category;
                showing_row = row;
                pressed = "";
            } else {
                showing_category = -1;
                showing_row = -1;
            }
        } else {
            showing_category = -1;
            showing_row = -1;
        }
    }
}

void keyPressed() {
    // w is 87
    // a is 65
    // s is 83
    // d is 68
    // f is 70
    // g is 71
    if (showing_category >= 0 && showing_category < 6) { 
        if (pressed == "") {
            if (keyCode == 87) { // w
                pressed = "A";
            } else if (keyCode == 71) { // g
                pressed = "B";
            } else if (keyCode == 32) {
                pressed = "answer";
            }
        } else if (pressed == "A") {
            if (keyCode == 89) { // y correct
                score_a += (showing_row + 1) * 100;
                pressed = "answer";
            } else if (keyCode == 78) { // n wrong
                score_a -= (showing_row + 1) * 100;
                pressed = "B";
            } else if (keyCode == 32) {
                pressed = "answer";
            }
        } else if (pressed == "B") {
            if (keyCode == 89) { // y correct
                score_b += (showing_row + 1) * 100;
                pressed = "answer";
            } else if (keyCode == 78) { // n wrong
                score_b -= (showing_row + 1) * 100;
                pressed = "A";
            } else if (keyCode == 32) {
                pressed = "answer";
            }
        } else if (pressed == "answer") {
            if (keyCode == 32) {
                boxes[showing_category][showing_row] = 1;
                pressed = "";
                showing_category = -1;
                showing_row = -1;
            }
        }
    } 
}

In [3]:
import processing.table.*;

Table table = loadTable("game3.csv", "header");
PFont fontA = loadFont("Arial");

String[] categories = new String[6];
int score_a = 0;
int score_b = 0;
int reveal = 0;
int[][] boxes = new int[6][5];
String[][] answers = new String[6][5];
String[][] questions = new String[6][5];
int showing_category = -1;
int showing_row = -1;
String pressed = "";

boolean arrayContains(String[] array, String search) {
    for (int i = 0; i < array.length; i++) {
        if (array[i] == search)
            return true;
    }
    return false;
}

void setup() {
    size(640, 480);
    // pick 6 unique categories:
    for (int i = 0; i < 6; i++) {
        int row_pos = int(random(0, table.getRowCount()));
        TableRow row = table.rows().get(row_pos);
        String cat = row.getString("Category");
        while (arrayContains(categories, cat)) {
            row_pos = int(random(0, table.getRowCount()));
            row = table.rows().get(row_pos);
            cat = row.getString("Category");
        }
        categories[i] = cat;
        // pick one q/a per topic/level:
        for (int j = 1; j <= 5; j++) {
            ArrayList choices = new ArrayList();
            int rows = 0;
            for (TableRow trow: table.rows()) {
                if (trow.getString("Category") == categories[i] && trow.getInt("Level") == j) {
                    choices.add(rows);
                }
                rows++;
            }
            if (choices.size() == 0) {
                println("Error in Category: " + categories[i] + ", level: " + j + ", count: " + choices.size());
            } else {
                // pick one
                int pickone = int(random(0, choices.size()));
                rows = choices.get(pickone);
                answers[i][j - 1] = table.rows().get(rows).getString("Answer");
                questions[i][j - 1] = table.rows().get(rows).getString("Question");
            }
        }
    }
    // Set up text defaults:
    textFont(fontA, 18);
    textAlign(CENTER, CENTER);
}

void draw() {
    int boxw = width/6.1;
    int boxh= height/8;
    background(127);
    fill(0);
    // categories:
    rect(5, 5, width - 10, boxh + 10);
    // q/a:
    rect(5, boxh * 1.5 - 5, width - 10, height - boxh - 70);
    // scores:
    rect(5, height - 40, width/2 - 10, 35);
    rect(width/2 + 5, height - 40, width/2 - 10, 35);
    fill(255, 201, 14); // yellow
    textAlign(LEFT, CENTER);
    text("Team A:", 5, height - 40, width/2 - 10, 35);
    text("Team B:", width/2 + 5, height - 40, width/2 - 10, 35);
    textAlign(RIGHT, CENTER);
    if (score_a >= 0) {
        text("$" + score_a, 5, height - 40, width/2 - 10, 35);
    } else {
        text("-$" + (-score_a), 5, height - 40, width/2 - 10, 35);
    }
    if (score_b >= 0) {
        text("$" + score_b, width/2 + 5, height - 40, width/2 - 10, 35);
    } else {
        text("-$" + (-score_b), width/2 + 5, height - 40, width/2 - 10, 35);
    }
    textAlign(CENTER, CENTER);
    // Boxes:
    for (int i=0; i < 6; i++) {
        fill(63, 72, 204); // blue
        rect(i * boxw + 10, 10, boxw - 10, boxh);
        fill(255, 201, 14); // yellow
        if (i < reveal)
            text(categories[i], i * boxw + 10, 5, boxw - 10, boxh);
    }
    for (int x=0; x < 6; x++) {
        for (int y=0; y < 5; y++) {
            fill(63, 72, 204); // blue
            rect(x * boxw + 10, y * (boxh + 10) + boxh * 1.5, boxw - 10, boxh);
            fill(255, 201, 14); // yellow
            if (x < reveal && boxes[x][y] == 0) {
                text("$" + ((y  + 1) * 100), 
                     x * boxw + 10, y * (boxh + 10) + boxh * 1.5, 
                     boxw - 10, boxh);
            }
        }
    }
    if (showing_category >= 0 && showing_row >= 0) {
        textAlign(CENTER, CENTER);
        fill(63/2, 72/2, 204/2); // blue
        rect(50, 50, width - 100, height - 150);
        fill(255, 201, 14); // yellow
        text(categories[showing_category] + " for $" + ((showing_row + 1) * 100), 50, 30, width - 100, 100);
        String answer = answers[showing_category][showing_row];
        textFont(fontA, 32);
        text(answer, 50, 50, width - 100, height - 150);
        textFont(fontA, 18);
        if (pressed == "A") {
            text("Team A buzzes in! Correct? y/n", 50, height - 200, width - 100, 100);
        } else if (pressed == "B") {
            text("Team B buzzes in! Correct? y/n", 50, height - 200, width - 100, 100);
        } else if (pressed == "answer") {
            text(questions[showing_category][showing_row], 50, height - 200, width - 100, 100);
        }
    }
}

void mousePressed() {
    int boxw = width/6.1;
    int boxh= height/8;
    if (reveal < 6) {
        reveal++;
    } else if (showing_category >= 0 && showing_row >= 0) {
        showing_category = -1;
        showing_row = -1;
    } else {
        // playing the game
        int category = int((mouseX - 10)/(boxw));
        int row = int((mouseY - boxh * 1.5)/(boxh + 10));
        //println("Category: " + category + " row: " + row);
        if (category >= 0 && category < 6) {
            if (row >= 0 && row < 5) {
                showing_category = category;
                showing_row = row;
                pressed = "";
            } else {
                showing_category = -1;
                showing_row = -1;
            }
        } else {
            showing_category = -1;
            showing_row = -1;
        }
    }
}

void keyPressed() {
    // w is 87
    // a is 65
    // s is 83
    // d is 68
    // f is 70
    // g is 71
    if (showing_category >= 0 && showing_category < 6) { 
        if (pressed == "") {
            if (keyCode == 87) { // w
                pressed = "A";
            } else if (keyCode == 71) { // g
                pressed = "B";
            } else if (keyCode == 32) {
                pressed = "answer";
            }
        } else if (pressed == "A") {
            if (keyCode == 89) { // y correct
                score_a += (showing_row + 1) * 100;
                pressed = "answer";
            } else if (keyCode == 78) { // n wrong
                score_a -= (showing_row + 1) * 100;
                pressed = "B";
            } else if (keyCode == 32) {
                pressed = "answer";
            }
        } else if (pressed == "B") {
            if (keyCode == 89) { // y correct
                score_b += (showing_row + 1) * 100;
                pressed = "answer";
            } else if (keyCode == 78) { // n wrong
                score_b -= (showing_row + 1) * 100;
                pressed = "A";
            } else if (keyCode == 32) {
                pressed = "answer";
            }
        } else if (pressed == "answer") {
            if (keyCode == 32) {
                boxes[showing_category][showing_row] = 1;
                pressed = "";
                showing_category = -1;
                showing_row = -1;
            }
        }
    } 
}